In [ ]:
import torch
import numpy as np

print(torch.__version__)

# Basics of PyTorch tensors

A [torch.Tensor](https://pytorch.org/docs/stable/tensors.html) is a multi-dimensional matrix containing elements of *a single data type*. They are similar to NumPy's ndarray with added functionality to take advantage of GPU's and auto-differentiation.

In [ ]:
a = torch.arange(6)
a

In [ ]:
a = torch.arange(6, dtype = torch.float32)
a

In [ ]:
torch.arange(6.0)

In [ ]:
a.shape

In [ ]:
a.type()

PyTorch has 12 different data types. Most functions that create tensors have a keyworded argument `dtype =` that can be used to specify a non-default type for the tensor.

https://pytorch.org/docs/stable/tensor_attributes.html#torch.torch.dtype

In [ ]:
a.dtype

In [ ]:
a.size()

In [ ]:
a = torch.arange(6).reshape(2,3)
a

In [ ]:
a.flatten()

In [ ]:
b_np = np.arange(12).reshape(3,4)
print(b_np)
b_np.ravel()

Use `from_numpy()` to create a Tensor from a numpy.ndarray that will share the same memory. The more general `as_tensor()` can create Tensors from any array_like data structure.

https://pytorch.org/docs/stable/generated/torch.from_numpy.html

https://pytorch.org/docs/stable/generated/torch.as_tensor.html#torch.as_tensor

Going from Tensor to numpy.ndarray can be done using `numpy()`, with the same conditions for sharing memory.

**It is important to know when a copy is performed vs. data is shared.**

In [ ]:
b_pt = torch.from_numpy(b_np)
b_pt

In [ ]:
b_pt[-1, -1] = 12
b_pt, b_np

In [ ]:
bnp = b_pt.numpy()
bnp

In [ ]:
bnp[-1, -1] = 11
bnp, b_pt

PyTorch is Python => the flexibility of dynamic typing, generic functions, automatic type casting, ...

In [ ]:
def sigmoid(x):
    return 1 / (1 + np.exp(-x))
sigmoid(b_pt)

In [ ]:
def sigmoid(x):
    return 1 / (1 + torch.exp(-x))
bexp = sigmoid(b_pt.type(torch.FloatTensor))
bexp, bexp.dtype

When possible, the reshaped tensor will be a *view* of the input tensor, otherwise, it will be a copy.

https://pytorch.org/docs/stable/generated/torch.reshape.html

https://pytorch.org/docs/stable/tensors.html#torch.Tensor.view

In [ ]:
b = b_pt.reshape(-1, 3)
b

In [ ]:
b[0,0] = -1.0
b, b_pt

In [ ]:
bt = b.t()
bt

In [ ]:
bt_flat = bt.reshape(-1)
bt_flat

In [ ]:
bt_flat[0] = 0
bt_flat, bt

Tensors that are stored on the GPU have a type that starts with `torch.cuda`. For example, tensors of type `torch.FloatTensor` are stored on the CPU, whereas `torch.cuda.FloatTensor` are stored on the GPU.

In [ ]:
if torch.cuda.is_available():
    b = b.cuda()
print(torch.cuda.is_available())
print(b, b.type())

# Example of computation graph 1

In [ ]:
# x = torch.tensor(2 * torch.ones(10.view(2,5), requires_grad = True)
x = torch.ones(2, 5, requires_grad = True)
print(x)
x.is_leaf

In [ ]:
y = x + 1
print(y)
y.is_leaf

In [ ]:
y.requires_grad

In [ ]:
z = 2 * y * y + x
z

In [ ]:
z.requires_grad

In [ ]:
out = z.mean()
out

In [ ]:
out.requires_grad

In [ ]:
out.backward()
print(x.grad)
print(y.grad)

## Use *retain_grad* to store gradients with non-leaf nodes

In [ ]:
x = torch.ones(10).view(2,5)
x.requires_grad_(True)
y = x + 1
y.retain_grad()
z = 2 * y * y + x
out = z.mean()
out.backward()

x.grad

In [ ]:
y.requires_grad

In [ ]:
y.grad

# Example of computation graph 2

In [ ]:
x = torch.tensor([1.0], requires_grad = True)
g1 = 3 * x
g1.requires_grad

In [ ]:
x = torch.tensor([1.0], requires_grad = True)
g1 = 3 * x
g2 = x ** 2 + x
h1 = 2 * g1 + 1
h2 = 2 * g1 + g2
loss = (h1 - h2) ** 2
print(loss)

In [ ]:
loss.backward()
x.grad, x.data, loss.grad_fn

In [ ]:
loss.backward()

## Set *retain_graph* to be able to reuse the graph after first call to *backward* 

In [ ]:
x = torch.tensor([1.0], requires_grad = True)
g1 = 3 * x
g2 = x ** 2 + x
h1 = 2 * g1 + 1
h2 = 2 * g1 + g2
loss = (h1 - h2) ** 2

loss.backward()
print(x.grad)

In [ ]:
x = torch.tensor([1.0], requires_grad = True)
g1 = 3 * x
g2 = x ** 2 + x
h1 = 2 * g1 + 1
h2 = 2 * g1 + g2
loss = (h1 - h2) ** 2

loss.backward(retain_graph = True)
print(x.grad)
loss.backward(retain_graph = True)
print(x.grad)

In [ ]:
# Rest gradients before calling backward()
x.grad.zero_()
loss.backward(retain_graph = True)
print(x.grad)

## Use *x.data* to get the underlying tensor of parameter *x*, useful for changing values in-place before calling *backward* on the same computation graph.
### See also this [PyTorch migration guide](https://pytorch.org/blog/pytorch-0_4_0-migration-guide/).

In [ ]:
x = torch.tensor([1.0], requires_grad = True)
g1 = 3 * x
g2 = x ** 2 + x
h1 = 2 * g1 + 1
h2 = 2 * g1 + g2
loss = (h1 - h2) ** 2

loss.backward(retain_graph = True)
print(x.grad)

# x[0] = 0.0 will lead to a RuntimeError, not allowed to change the value of a variable needed for gradient computation.
# Use x.data instead, shares the same tensor, but no computation history.
x.data[0] = 0.0
g1 = 3 * x
g2 = x ** 2 + x
h1 = 2 * g1 + 1
h2 = 2 * g1 + g2
loss = (h1 - h2) ** 2

loss.backward(retain_graph = True)
print(x.grad)

# General *autograd* with vector-Jacobian products
### vector $x \rightarrow$ vector $z(x) \rightarrow$ scalar $L(z)$
### $\displaystyle\frac{\delta L}{\delta x} =$ vector $\times$ Jacobian $= \displaystyle\frac{\delta L}{\delta z} \times \frac{\delta z}{\delta x}$

In [ ]:
x = 2 * torch.ones(10).view(2,5)
x.requires_grad_(True)
y = x + 1
z = 2 * y * y + x
out = z.mean()
out.backward(retain_graph = True)

print(x.grad)
print(x.grad.type())
print(x.grad.dtype)

In [ ]:
# Now compute gradient of z (each element in z) with respect to x.
# Not working because z is not a scalar, requires argument that is
# gradient with respect to z (same shape as z).
x.grad.zero_()
z.backward(retain_graph = True)

In [ ]:
# Now compute gradient of z (each element in z) with respect to x.
# Assume gradient wrt z is 1.
z.backward(torch.ones(10).view(2,-1), retain_graph = True)
x.grad

In [ ]:
# Now compute gradient of z (each element in z) with respect to x.
# Assume gradient wrt z is 2.
x.grad.zero_()
z.backward(2 * torch.ones(10).view(2,-1), retain_graph = True)
x.grad